In [ ]:
import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"

# Sozialversicherungsbeiträge

In dieser Übung fügen Sie die Sozialversicherungsbeiträge den Steuern, die wir in den letzten Vorlesungen berechnet hatten, hinzu.

Wir konzentrieren uns auf die Überweisungsbeträge am Ende jeden Monats, d.h., die Lohnsteuer. Dabei ignorieren wir jegliche Vorwegabzüge oder Pauschalen (in der Realität wird zum Beispiel die Werbungskostenpauschale von 1000 € jährlich bereits einbezogen).

Zunächst eine Wiederholung der Funktionen aus den letzten Wochen und eine neue Funktion, die die Lohnsteuer für das *monatliche* Einkommen berechnet.

In [ ]:
def einkommensteuer_2023(zu_versteuerndes_einkommen):
    """Einkommensteuer 2023.

    Args:
        zu_versteuerndes_einkommen (float): Zu versteuerndes Einkommen

    Output:
        Steuerlast(float): Steuerlast 2023
    """
    x = np.floor(zu_versteuerndes_einkommen)
    y = (x - 10_908) / 10_000
    z = (x - 15_999) / 10_000

    if x <= 10_908:
        return 0
    elif x <= 15_999:
        return np.floor((979.18 * y + 1_400) * y)
    elif x <= 62_809:
        return np.floor((192.59 * z + 2_397) * z + 966.53)
    elif x <= 277_825:
        return np.floor(0.42 * x - 9_972.98)
    else:
        return np.floor(0.45 * x - 18_307.73)


def soli(einkommensteuer, freigrenze, soli_rate_max):
    """Solidaritätszuschlag.

    Args:
        einkommensteuer (float): Einkommensteuerlast
        freigrenze (float): Solidaritätszuschlagsfreigrenze für die Einkommensteuerlast
        soli_rate_max (float): Maximaler Grenzsteuersatz des Solidaritätszuschlags

    Output:
        soli (float): Steuerlast aus dem Solidaritätszuschlag
    """
    soli = np.minimum(
        0.055 * einkommensteuer,
        np.maximum(soli_rate_max * (einkommensteuer - freigrenze), 0),
    )

    return soli


def lohnsteuer(einkommen_monatlich):
    """Monatliche Lohnsteuerbeträge aus Einkommensteuer und Solidaritätszuschlag.

    Ignoriere jegliche Vorwegabzüge und Pauschalen.

    """
    e_st = einkommensteuer_2023(zu_versteuerndes_einkommen=einkommen_monatlich * 12)
    soli_betrag = soli(einkommensteuer=e_st, freigrenze=16_956, soli_rate_max=0.119)

    return np.round((e_st + soli_betrag) / 12, 2)

## Anwendung

Wir beschäftigent uns mit folgenden monatlichen Einkommen von kinderlosen, in Westdeutschland lebenden Singles,
deren Krankenversicherung keine Zusatzbeiträge erhebt. Diejenigen mit Einkommen jenseits der Pflichtversicherungsgrenze
sind freiwillige Mitglieder in der gesetzlichen Krankenversicherung.

Die niedrigste betrachtete Einkommensstufe wird durch den Mindestlohn bestimmt. Hierfür benutzen wir den typischen Fall
von Arbeitsverträgen in Deutschland, nämlich dem Ausgleich der von Monat zu Monat variierenden Arbeitstage durch das
sogenannte "verstetigte Monatsgehalt", welches die Zahl der Wochen im Jahr gleichmäßig auf alle Monate aufteilt und so
auf 173,33 Arbeitsstunden pro Monat kommt.

Die Lohnsteuer haben wir bereits hinzugefügt.

In [ ]:
mindestlohn_stunde = 12
stunden_monat = 40 * 52 / 12

data = pd.DataFrame(
    {
        "einkommen_m": [
            np.round(stunden_monat * mindestlohn_stunde, 0),
            2500,
            3000,
            4000,
            5000,
            6000,
            7500,
            10000,
            15000,
        ],
    },
)
data["lohnsteuerlast"] = data["einkommen_m"].apply(lohnsteuer)
data

## Generische Funktion für Sozialversicherungsbeiträge von Arbeitnehmern

Die folgende Funktion können Sie nutzen, um die Beiträge zu den verschiedenen Sozialversicherungen
zu berechnen. Sie brauchen nichts komplizierter zu machen, als Sie es hier sehen. Sollten wir in der
Aufgabenstellung einen Spezialfall übersehen haben, geben Sie uns bitte kurz Bescheid.

In [ ]:
def soz_vers_beitrag(
    einkommen_m,
    arbeitnehmersatz,
    bemessungsgrenze_m,
):
    """Beitrag zu einer der Sozialversicherungen.

    Inputs:

        einkommen_m (float): Monatliches Bruttoeinkommen
        arbeitnehmersatz (float): Beitragssatz, der vom Arbeitnehmer zu zahlen ist
        bemessungsgrenze_m (float): Monatliche Beitragsbemessungsgrenze

    Output:

        arbeitnehmerbeitrag (float): Der Beitrag in Euro zur Sozialversicherung.

    """
    e_bis_bbg = np.minimum(einkommen_m, bemessungsgrenze_m)
    arbeitnehmerbeitrag = e_bis_bbg * arbeitnehmersatz

    return np.round(arbeitnehmerbeitrag, 2)

## Aufgabe 1

Fügen Sie die relevanten Sozialversicherungsbeiträge in einzelnen Spalten zur Tabelle hinzu und benennen Sie die Spalten entsprechend: z.B. `arbeitslosenv_beitrag`.

Eine schöne Übersicht finden Sie zum Beispiel hier: http://www.sozialpolitik-aktuell.de/tl_files/sozialpolitik-aktuell/_Politikfelder/Sozialstaat/Datensammlung/PDF-Dateien/tabIII15.pdf

## Aufgabe 2

Fügen Sie die Gesamtbelastung der Arbeitseinkommen mit Steuern und Sozialversicherungen als Spalte hinzu. Nennen Sie die Spalte `gesamtbelastung`.

## Aufgabe 3

Berechnen Sie die Steuer- und Abgabenquote und nennen Sie die Spalte `steuer_abgaben_quote`.

Führen Sie die folgende Zelle aus, um die Steuer- und Abgabenquote zu plotten.

In [ ]:
fig = data.plot.bar(x="steuer_abgaben_quote", y="einkommen_m", orientation="h")
fig.update_yaxes(type="category")
fig.update_layout(
    xaxis_title="Steuer- und Abgabenquote",
    yaxis_title="Monatliches Bruttoeinkommen",
)
fig.show()

## Aufgaben in der Präsenzphase

## Aufgabe 1 (20 Minuten)

## Aufgabe 2 (100 Minuten)

### Aufgabe 2.1 (20 Minuten)


### Aufgabe 2.2 (30 Minuten)

### Aufgabe 2.3 (30 Minuten)

### Aufgabe 2.4 (20 Minuten)

## Aufgabe 3: Pentabilities (10min)